In [7]:
import torch
from transformers import BertTokenizer, BertForSequenceClassification
from torch.optim import AdamW
from torch.utils.data import DataLoader, TensorDataset
import torch.nn.functional as F


In [8]:
pretrained_model_name = 'bert-base-uncased'
tokenizer = BertTokenizer.from_pretrained(pretrained_model_name)
model = BertForSequenceClassification.from_pretrained(pretrained_model_name,
                                                      num_labels=2)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Falling back to regular HTTP download. For better performance, install the package with: `pip install huggingface_hub[hf_xet]` or `pip install hf_xet`


model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [9]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e

In [10]:
train_texts = [
    "I love this product, it's amazing!",  # Positive
    "Absolutely fantastic experience, will buy again!",  # Positive
    "Worst purchase ever. Completely useless.",  # Negative
    "I hate this item, it doesn't work!",  # Negative
    "The quality is top-notch, highly recommend!",  # Positive
    "Terrible service, never coming back.",  # Negative
    "This is the best thing I've ever bought!",  # Positive
    "Very disappointing. Waste of money.",  # Negative
    "Superb! Exceeded all my expectations.",  # Positive
    "Not worth the price at all.",  # Negative
]
train_labels = torch.tensor([1, 1, 0, 0, 1, 0, 1, 0, 1, 0]).to(device)

In [11]:
encoded_train = tokenizer(train_texts,
                          padding=True,
                          truncation=True,
                          max_length=128,
                          return_tensors='pt')
train_input_ids = encoded_train['input_ids'].to(device)
train_attention_masks = encoded_train['attention_mask'].to(device)

In [12]:
train_dataset = TensorDataset(train_input_ids, train_attention_masks, train_labels)
train_loader = DataLoader(train_dataset, batch_size=2, shuffle=True)

In [13]:
optimizer = AdamW(model.parameters(), lr=2e-5)

In [14]:
epochs = 5
model.train()
for epoch in range(epochs):
    total_loss = 0
    correct = 0
    total = 0

    for batch in train_loader:
        batch_input_ids, batch_attention_masks, batch_labels = batch

        optimizer.zero_grad()
        outputs = model(input_ids=batch_input_ids,
                        attention_mask=batch_attention_masks,
                        labels=batch_labels)

        loss = outputs.loss
        logits = outputs.logits

        total_loss += loss.item()
        loss.backward()
        optimizer.step()

        preds = torch.argmax(F.softmax(logits, dim=1), dim=1)
        correct += (preds == batch_labels).sum().item()
        total += batch_labels.size(0)

    avg_loss = total_loss / len(train_loader)
    accuracy = correct / total * 100
    print(f"Epoch {epoch+1} - Loss: {avg_loss:.4f}, Accuracy: {accuracy:.2f}%")


Epoch 1 - Loss: 0.7286, Accuracy: 50.00%
Epoch 2 - Loss: 0.5729, Accuracy: 70.00%
Epoch 3 - Loss: 0.4060, Accuracy: 100.00%
Epoch 4 - Loss: 0.2441, Accuracy: 100.00%
Epoch 5 - Loss: 0.1898, Accuracy: 100.00%


In [15]:
torch.save(model.state_dict(), "fine_tuned_bert.pth")

In [16]:
model.load_state_dict(torch.load("fine_tuned_bert.pth"))
model.to(device)

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e

In [17]:
test_texts = [
    "This is a great product, I love it!",  # Positive
    "Horrible experience, I want a refund!",  # Negative
    "Highly recommended! Five stars.",  # Positive
    "Not worth it. I regret buying this.",  # Negative
]
test_labels = torch.tensor([1, 0, 1, 0]).to(device)

encoded_test = tokenizer(test_texts,
                         padding=True,
                         truncation=True,
                         max_length=128,
                         return_tensors='pt')

test_input_ids = encoded_test['input_ids'].to(device)
test_attention_masks = encoded_test['attention_mask'].to(device)

In [18]:
model.eval()
with torch.no_grad():
    outputs = model(input_ids=test_input_ids,
                    attention_mask=test_attention_masks)
    predicted_labels = torch.argmax(outputs.logits, dim=1)

test_accuracy = (predicted_labels == test_labels).sum().item() / len(test_labels) * 100
print(f"\nTest Accuracy: {test_accuracy:.2f}%")

for text, label in zip(test_texts, predicted_labels):
    print(f'Text: {text}\nPredicted Label: {label.item()}\n')



Test Accuracy: 75.00%
Text: This is a great product, I love it!
Predicted Label: 1

Text: Horrible experience, I want a refund!
Predicted Label: 1

Text: Highly recommended! Five stars.
Predicted Label: 1

Text: Not worth it. I regret buying this.
Predicted Label: 0

